# 2-Dimensional single cell example

- How to couple the physical model with IBM

- Go through the whole processes of runing the model and visualization

## For more documentation
- <https://zhenwu0728.github.io/PlanktonIndividuals.jl/dev/> for PlanktonIndividuals.jl
- <https://clima.github.io/Oceananigans.jl/stable/> for Oceananigans.jl
- <http://docs.juliaplots.org/latest/> for Plots.jl
- <https://docs.julialang.org/en/v1/> for Julia

## 1. Load `Julia` packages

In [1]:
using PlanktonIndividuals, Oceananigans, YAML, Plots

┌ Info: Precompiling Plots [91a5bcdd-55d7-5caf-9e0b-520d859cae80]
└ @ Base loading.jl:1260


## 2. Model initialization
### 2.1 Physical model initialization

In [2]:
Nx = 25       # Number of grid points in x and y
Nz = 50       # Number of grid points in z
Δz = 4.0      # Grid spacing in x, y, z (meters)
Qᵀ = 1e-5     # Temperature flux at surface
∂T∂z = 0.005  # Initial vertical temperature gradient
f = 1e-4      # Coriolis parameter
α = 2e-4      # Thermal expansion coefficient
β = 8e-4      # Haline contraction coefficient

grids = RegularCartesianGrid(size=(Nx, 1, Nz), extent=(Δz*Nx, Δz*Nx, Δz*Nz))
T_bcs = TracerBoundaryConditions(grids, top = BoundaryCondition(Flux, Qᵀ), bottom = BoundaryCondition(Gradient, ∂T∂z))

model = IncompressibleModel(
                 architecture = CPU(),
                         grid = grids,
                     coriolis = FPlane(f=f),
                     buoyancy = SeawaterBuoyancy(equation_of_state=LinearEquationOfState(α=α, β=β)),
                      closure = AnisotropicMinimumDissipation(),
          boundary_conditions = (T=T_bcs,)
)

## Random noise damped at top and bottom
Ξ(z) = randn() * z / model.grid.Lz * (1 + z / model.grid.Lz) # noise

## Temperature initial condition: a stable density tradient with random noise superposed.
T₀(x, y, z) = 20 + ∂T∂z * z + ∂T∂z * model.grid.Lz * 1e-6 * Ξ(z)

set!(model, T=T₀)
wizard = TimeStepWizard(cfl=0.2, Δt=1.0, max_change=1.1, max_Δt=60.0);

### 2.1 Physical model warm up

In [3]:
# warm up of physical model
simulation = Simulation(model, Δt=wizard, stop_iteration=400*40, progress_frequency=200)
run!(simulation)

Nsimulation = Simulation(model, Δt=10.0, stop_iteration=16002, progress_frequency=2)

┌ Info: Simulation is stopping. Model iteration 16000 has hit or exceeded simulation stop iteration 16000.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22


Simulation{IncompressibleModel{CPU, Float64}}
├── Model clock: time = 3.846 day, iteration = 16000 
├── Next time step (Float64): 10.000 s 
├── Progress frequency: 2
├── Stop criteria: Any[Oceananigans.Simulations.iteration_limit_exceeded, Oceananigans.Simulations.stop_time_exceeded, Oceananigans.Simulations.wall_time_limit_exceeded]
├── Run time: 0.000 s, wall time limit: Inf
├── Stop time: Inf day, stop iteration: 16002
├── Diagnostics: OrderedCollections.OrderedDict with no entries
└── Output writers: OrderedCollections.OrderedDict with no entries

### 2.2 IBM initialization

In [4]:
resultpath = PrepRunDir()
phy_grid = read_Ogrids(grids);
nday = 2
RunParam.nTime = 1440*nday # simulated days in minute
RunParam.ΔT = 60 # model time step: 60 seconds

# update paramters
phy_params = YAML.load(open("params.yml"))
update_params!(RunParam.params,phy_params)
RunParam.params["P_Nind"] = 1
RunParam.params["Grz_P"] = 0

# Initial conditions
#           DIC  NH4   NO3   PO4   DOC  DON  DOP  POC  PON  POP  ZOO
nut_init = [2.0, 0.05, 0.10, 0.02, 1.0, 0.1, 0.1, 1.0, 0.1, 0.1, 2.0];
phy_model = PI_Model(phy_grid, RunParam;
                     nutrients = setup_nutrients(phy_grid,nut_init));

# the depth of the individual
phy_model.individuals.phytos[3,:] = rand(collect(-30.0:0.1:-2.0),1);

### 3. Run the model
- **Velocities will be passed to IBM to advect individuals and nutrient tracers**
- RK4 is used for the advection of individuals

In [5]:
anim = @animate for i in 1:1440*nday
    vel_field =[]
    for j in 1:3
        run!(Nsimulation)
        Nsimulation.stop_iteration += 2
        u = model.velocities.u.data.parent
        v = model.velocities.v.data.parent
        w = model.velocities.w.data.parent
        vel = PlanktonIndividuals.velocity(u, v, w)
        push!(vel_field,vel)
    end
    vel_itps = (generate_vel_itp(phy_model.grid, vel_field[1]),
                generate_vel_itp(phy_model.grid, vel_field[2]),
                generate_vel_itp(phy_model.grid, vel_field[3]))
    PI_advectRK4!(phy_model, RunParam.ΔT, vel_itps)
    PI_TimeStep!(phy_model, RunParam.ΔT, vel_field[end], resultpath)

    phyts_sp = sort_species(phy_model.individuals.phytos, phy_model.params["P_Nsp"])
    write_species_dynamics(phy_model.t, phyts_sp, resultpath)
    
    # ploting
    w = Array(interior(model.velocities.w))[:, 1, :]
    p1 = Plots.heatmap(phy_model.grid.xC[2:end-1], phy_model.grid.zF[2:end-1], w',xlabel="x (m)", ylabel="z (m)",clims=(-4e-2, 4e-2),color=:balance, fill=true)
    Plots.scatter!(p1, phyts_sp[1][1,:],phyts_sp[1][3,:], markersize=7,markercolor=:lime, xlims=(0,100), ylims=(-200,0), xlabel="x (m)", ylabel="z (m)", cbar=false, legend=:none)
    Plots.plot(p1, size=(300, 600),title=lpad(i÷1440,2,"0")*"day "*lpad(i÷60-24*(i÷1440),2,"0")*"hour")
end

┌ Info: Simulation is stopping. Model iteration 16002 has hit or exceeded simulation stop iteration 16002.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16004 has hit or exceeded simulation stop iteration 16004.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16006 has hit or exceeded simulation stop iteration 16006.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16008 has hit or exceeded simulation stop iteration 16008.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16010 has hit or exceeded simulation stop iteration 16010.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia

┌ Info: Simulation is stopping. Model iteration 16086 has hit or exceeded simulation stop iteration 16086.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16088 has hit or exceeded simulation stop iteration 16088.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16090 has hit or exceeded simulation stop iteration 16090.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16092 has hit or exceeded simulation stop iteration 16092.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16094 has hit or exceeded simulation stop iteration 16094.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia

┌ Info: Simulation is stopping. Model iteration 16170 has hit or exceeded simulation stop iteration 16170.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16172 has hit or exceeded simulation stop iteration 16172.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16174 has hit or exceeded simulation stop iteration 16174.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16176 has hit or exceeded simulation stop iteration 16176.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16178 has hit or exceeded simulation stop iteration 16178.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia

┌ Info: Simulation is stopping. Model iteration 16254 has hit or exceeded simulation stop iteration 16254.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16256 has hit or exceeded simulation stop iteration 16256.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16258 has hit or exceeded simulation stop iteration 16258.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16260 has hit or exceeded simulation stop iteration 16260.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16262 has hit or exceeded simulation stop iteration 16262.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia

┌ Info: Simulation is stopping. Model iteration 16334 has hit or exceeded simulation stop iteration 16334.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16336 has hit or exceeded simulation stop iteration 16336.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16338 has hit or exceeded simulation stop iteration 16338.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16340 has hit or exceeded simulation stop iteration 16340.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 16342 has hit or exceeded simulation stop iteration 16342.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia

...

┌ Info: Simulation is stopping. Model iteration 20618 has hit or exceeded simulation stop iteration 20618.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20620 has hit or exceeded simulation stop iteration 20620.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20622 has hit or exceeded simulation stop iteration 20622.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20624 has hit or exceeded simulation stop iteration 20624.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20626 has hit or exceeded simulation stop iteration 20626.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia

┌ Info: Simulation is stopping. Model iteration 20702 has hit or exceeded simulation stop iteration 20702.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20704 has hit or exceeded simulation stop iteration 20704.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20706 has hit or exceeded simulation stop iteration 20706.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20708 has hit or exceeded simulation stop iteration 20708.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20710 has hit or exceeded simulation stop iteration 20710.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia

┌ Info: Simulation is stopping. Model iteration 20786 has hit or exceeded simulation stop iteration 20786.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20788 has hit or exceeded simulation stop iteration 20788.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20790 has hit or exceeded simulation stop iteration 20790.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20792 has hit or exceeded simulation stop iteration 20792.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20794 has hit or exceeded simulation stop iteration 20794.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia

┌ Info: Simulation is stopping. Model iteration 20870 has hit or exceeded simulation stop iteration 20870.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20872 has hit or exceeded simulation stop iteration 20872.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
Excessive output truncated after 524600 bytes.┌ Info: Simulation is stopping. Model iteration 20874 has hit or exceeded simulation stop iteration 20874.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22
┌ Info: Simulation is stopping. Model iteration 20876 has hit or exceeded simulation stop iteration 20876.
└ @ Oceananigans.Simulations /Users/zhenwu/.julia/packages/Oceananigans/V3Ec3/src/Simulations/run.jl:22


Animation("/var/folders/pb/sxn625r94w77bfkfp_frz08r0000gn/T/jl_FN4BOF", ["000001.png", "000002.png", "000003.png", "000004.png", "000005.png", "000006.png", "000007.png", "000008.png", "000009.png", "000010.png"  …  "002871.png", "002872.png", "002873.png", "002874.png", "002875.png", "002876.png", "002877.png", "002878.png", "002879.png", "002880.png"])

In [6]:
mp4(anim, "motions.mp4", fps = 60)

┌ Info: Saved animation to 
│   fn = /Users/zhenwu/Zhen_WU/PlanktonIndividualsExamples/motions.mp4
└ @ Plots /Users/zhenwu/.julia/packages/Plots/Xnzc7/src/animation.jl:104


Plots.AnimatedGif("/Users/zhenwu/Zhen_WU/PlanktonIndividualsExamples/motions.mp4")

## 4. Things to do next...
1. Different heat flux $Q^T$
2. Different location of the individual